In [ ]:
!pip install transformers
!pip install accelerate
!pip install Korpora
!pip3 install kobert-transformers
!pip install ipywidgets

In [ ]:
import torch
from transformers import BertForSequenceClassification
from kobert_transformers import get_tokenizer

# 모델과 토크나이저를 불러옵니다.
model_name = 'skt/kobert-base-v1'
tokenizer = get_tokenizer()
model = BertForSequenceClassification.from_pretrained(model_name, num_labels=2)

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

model.to(device)

In [ ]:
from torch.utils.data import Dataset, DataLoader
from Korpora import Korpora
corpus = Korpora.load("nsmc")

# 코퍼스에서 train 데이터를 추출합니다.
texts = []
labels = []
for data in corpus.train:
    texts.append(data.text)
    labels.append(data.label)

print(f"\n입력 데이터")
print(f"text: {texts[0]}, label: {labels[0]}")
print(f"text: {texts[1]}, label: {labels[1]}")

In [ ]:
# 데이터 세트 클래스를 상속받아 새로운 클래스를 생성합니다.
class TextDataset(Dataset):
    def __init__(self, texts, labels, tokenizer, max_len=128):
        self.texts = texts
        self.labels = labels
        self.tokenizer = tokenizer
        self.max_len = max_len

    def __len__(self):
        return len(self.texts)

    def __getitem__(self, idx):
        text = self.texts[idx]
        label = self.labels[idx]
        inputs = self.tokenizer(
            text,
            max_length=self.max_len,
            padding='max_length',
            truncation=True,
            return_tensors='pt'
        )
        input_ids = inputs['input_ids'].squeeze()
        attention_mask = inputs['attention_mask'].squeeze()

        return {
            'input_ids': input_ids,
            'attention_mask': attention_mask,
            'labels': torch.tensor(label, dtype=torch.long)
        }

# Dataset과 DataLoader 준비합니다.
dataset = TextDataset(texts[:15000], labels[:15000], tokenizer)
loader = DataLoader(dataset, batch_size=128, shuffle=True)

In [ ]:
from torch.optim import AdamW
from tqdm.notebook import tqdm

# 옵티마이저 설정합니다.
optimizer = AdamW(model.parameters(), lr=5e-5)

model.train()

# 훈련을 진행합니다.
for epoch in range(3):  # 에폭 수는 필요에 따라 조절해야 하지만 시간상 3으로만 진행합니다.
    for batch in tqdm(loader):
        optimizer.zero_grad()
        input_ids = batch['input_ids']
        attention_mask = batch['attention_mask']
        labels = batch['labels']

        outputs = model(input_ids.to(device), attention_mask=attention_mask.to(device), labels=labels.to(device))
        loss = outputs.loss
        loss.backward()
        optimizer.step()

        tqdm.write(f"Batch Loss: {loss.item()}")

In [ ]:
# 코퍼스에서 train 데이터를 추출합니다.
texts = []
labels = []
for data in corpus.test:
    texts.append(data.text)
    labels.append(data.label)

# Dataset과 DataLoader 준비합니다.
dataset = TextDataset(texts[:5000], labels[:5000], tokenizer)
loader = DataLoader(dataset, batch_size=1, shuffle=False)

In [ ]:
# 평가를 진행합니다.
model.eval()
correct = 0
with torch.no_grad():
    for batch in tqdm(loader):
        input_ids = batch['input_ids']
        attention_mask = batch['attention_mask']
        labels = batch['labels']

        outputs = model(input_ids.to(device), attention_mask=attention_mask.to(device))

        if torch.argmax(outputs.logits.cpu()) == labels: correct += 1

print(f"acc: {correct / len(loader)}")